<a href="https://colab.research.google.com/github/douglasmmachado/MedicineConsumption/blob/main/notebooks/causal_method/unified_approach/5_Forecasting.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 5 - Forecasting and prediction



---



---



In [21]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from scipy import stats
import seaborn as sns
import math as m

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor

from sklearn.tree import export_graphviz
from subprocess import call
from IPython.display import Image

from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error,  mean_absolute_percentage_error
from sklearn.model_selection import RandomizedSearchCV
from sklearn.preprocessing import StandardScaler

from sklearn.utils import shuffle
from sklearn.model_selection import GridSearchCV


df_agg_clusters_url = "https://raw.githubusercontent.com/douglasmmachado/MedicineConsumption/main/datasets/unified_approach/clustered/df_clustered.csv"
df_url = "https://raw.githubusercontent.com/douglasmmachado/ExploratoryDataAnalysis/main/datasets/unified_approach/df_ma.csv"
df_clustered_pca_url = "https://raw.githubusercontent.com/douglasmmachado/MedicineConsumption/main/datasets/unified_approach/clustered/df_clustered_pca.csv"

df = pd.read_csv(df_url)
df_agg_clusters = pd.read_csv(df_agg_clusters_url)
df_clustered_pca = pd.read_csv(df_clustered_pca_url)


# Convert numerical columns to string
for i, curr_df in enumerate([df, df_agg_clusters]):
    numerical_columns = ['HOSPI_CODE_UCD']
    curr_df[numerical_columns] = curr_df[numerical_columns].astype('string')


medicines = ['3400892088310','3400892075761','3400892203645',
             '3400892065366','3400892052120','3400891996128',
             '3400893826706','3400893736135','3400893875490',
             '3400890837149','3400891235203','3400891225037',
             '3400891191226','3400892729589','3400892745848',
             '3400892697789','3400892761527','3400893022634',
             '3400892761695','3400892669236','3400892508566']

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6636 entries, 0 to 6635
Data columns (total 39 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   DATE            6636 non-null   object 
 1   HOSPI_CODE_UCD  6636 non-null   string 
 2   LIT_HC          6636 non-null   float64
 3   LIT_HP          6636 non-null   float64
 4   N_ETB           6636 non-null   float64
 5   N_UFS           6636 non-null   float64
 6   PN_MEDICAL      6636 non-null   float64
 7   POPULATION      6636 non-null   float64
 8   P_MEDICAL       6636 non-null   float64
 9   QUANTITY        6636 non-null   float64
 10  QUANTITY_MA     6636 non-null   float64
 11  RESID           6636 non-null   float64
 12  SEASONAL        6636 non-null   float64
 13  SEJ_HAD         6636 non-null   float64
 14  SEJ_MCO         6636 non-null   float64
 15  SEJ_PSY         6636 non-null   float64
 16  SEJ_SLD         6636 non-null   float64
 17  SEJ_SSR         6636 non-null   f

In [4]:
df_agg_clusters.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6320 entries, 0 to 6319
Data columns (total 40 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   DATE            6320 non-null   object 
 1   HOSPI_CODE_UCD  6320 non-null   string 
 2   LIT_HC          6320 non-null   float64
 3   LIT_HP          6320 non-null   float64
 4   N_ETB           6320 non-null   float64
 5   N_UFS           6320 non-null   float64
 6   PN_MEDICAL      6320 non-null   float64
 7   POPULATION      6320 non-null   float64
 8   P_MEDICAL       6320 non-null   float64
 9   QUANTITY        6320 non-null   float64
 10  QUANTITY_MA     6320 non-null   float64
 11  RESID           6320 non-null   float64
 12  SEASONAL        6320 non-null   float64
 13  SEJ_HAD         6320 non-null   float64
 14  SEJ_MCO         6320 non-null   float64
 15  SEJ_PSY         6320 non-null   float64
 16  SEJ_SLD         6320 non-null   float64
 17  SEJ_SSR         6320 non-null   f

In [22]:
df_agg_clusters = df_agg_clusters[df_agg_clusters['QUANTITY'] > 0]
df_agg_clusters.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3867 entries, 4 to 6318
Data columns (total 40 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   DATE            3867 non-null   object 
 1   HOSPI_CODE_UCD  3867 non-null   string 
 2   LIT_HC          3867 non-null   float64
 3   LIT_HP          3867 non-null   float64
 4   N_ETB           3867 non-null   float64
 5   N_UFS           3867 non-null   float64
 6   PN_MEDICAL      3867 non-null   float64
 7   POPULATION      3867 non-null   float64
 8   P_MEDICAL       3867 non-null   float64
 9   QUANTITY        3867 non-null   float64
 10  QUANTITY_MA     3867 non-null   float64
 11  RESID           3867 non-null   float64
 12  SEASONAL        3867 non-null   float64
 13  SEJ_HAD         3867 non-null   float64
 14  SEJ_MCO         3867 non-null   float64
 15  SEJ_PSY         3867 non-null   float64
 16  SEJ_SLD         3867 non-null   float64
 17  SEJ_SSR         3867 non-null   f

In [23]:
df = df[(df['QUANTITY'] > 0)]
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 4072 entries, 4 to 6634
Data columns (total 39 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   DATE            4072 non-null   object 
 1   HOSPI_CODE_UCD  4072 non-null   string 
 2   LIT_HC          4072 non-null   float64
 3   LIT_HP          4072 non-null   float64
 4   N_ETB           4072 non-null   float64
 5   N_UFS           4072 non-null   float64
 6   PN_MEDICAL      4072 non-null   float64
 7   POPULATION      4072 non-null   float64
 8   P_MEDICAL       4072 non-null   float64
 9   QUANTITY        4072 non-null   float64
 10  QUANTITY_MA     4072 non-null   float64
 11  RESID           4072 non-null   float64
 12  SEASONAL        4072 non-null   float64
 13  SEJ_HAD         4072 non-null   float64
 14  SEJ_MCO         4072 non-null   float64
 15  SEJ_PSY         4072 non-null   float64
 16  SEJ_SLD         4072 non-null   float64
 17  SEJ_SSR         4072 non-null   f

In [24]:
df_clustered_pca.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6320 entries, 0 to 6319
Data columns (total 40 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   DATE            6320 non-null   object 
 1   HOSPI_CODE_UCD  6320 non-null   int64  
 2   LIT_HC          6320 non-null   float64
 3   LIT_HP          6320 non-null   float64
 4   N_ETB           6320 non-null   float64
 5   N_UFS           6320 non-null   float64
 6   PN_MEDICAL      6320 non-null   float64
 7   POPULATION      6320 non-null   float64
 8   P_MEDICAL       6320 non-null   float64
 9   QUANTITY        6320 non-null   float64
 10  QUANTITY_MA     6320 non-null   float64
 11  RESID           6320 non-null   float64
 12  SEASONAL        6320 non-null   float64
 13  SEJ_HAD         6320 non-null   float64
 14  SEJ_MCO         6320 non-null   float64
 15  SEJ_PSY         6320 non-null   float64
 16  SEJ_SLD         6320 non-null   float64
 17  SEJ_SSR         6320 non-null   f

## 5.1 - New database composition based on clusters

## 5.2 - Building forecasting models based on clusters

In [10]:
import plotly.graph_objects as go

def plot_pred(y_pred, y_test, medicine):
    # Create a scatter plot for y_pred
    fig = go.Figure(data=go.Scatter(x=np.arange(len(y_pred)), y=y_pred, mode='markers', name='y_pred', marker=dict(symbol='circle')))

    # Add scatter plot for y_test
    fig.add_trace(go.Scatter(x=np.arange(len(y_test)), y=y_test, mode='markers', name='y_test', marker=dict(symbol='x')))

    # Set axes labels and title
    fig.update_layout(xaxis_title='Test samples', yaxis_title='Quantity',
                      title=f'y_pred and y_test for medicine: {medicine}')

    # Show the plot
    fig.show()


In [11]:
import plotly.graph_objects as go

def plot_mape(y_pred, y_test, medicine, epsilon=0.001):
    mape_array = np.abs(y_test - y_pred) / np.maximum(epsilon, np.abs(y_test))

    # Create a scatter plot for MAPE
    fig = go.Figure(data=go.Scatter(x=np.arange(len(y_pred)), y=mape_array, mode='markers', name='MAPE'))

    # Set axes labels and title
    fig.update_layout(xaxis_title='Test samples', yaxis_title='MAPE',
                      title=f'MAPE for medicine: {medicine}')

    # Show the plot
    fig.show()


In [26]:
def test_1_baseline(df, medicine, df_scores):
  print()
  print(100*'-')
  print('Medicine:' + str(medicine))

  X = df[df['HOSPI_CODE_UCD'] == medicine].drop(['QUANTITY', 'HOSPI_CODE_UCD', 'DATE', 'QUANTITY_MA', 'RESID', 'SEASONAL', 'TREND'], axis=1).values

  scaler = StandardScaler()
  X_scaled = scaler.fit_transform(X)

  y = df[df['HOSPI_CODE_UCD'] == medicine]['QUANTITY'].values

  X_scaled, y = shuffle(X_scaled, y, random_state=42)

  if m.ceil(len(X_scaled) * 0.1) == 1:
    print('Dataset too small')
    test_size = 2
  else:
    test_size = 0.1

  # Split the data into training and testing sets
  X_train, X_test, y_train, y_test = train_test_split(X_scaled, y,
                                                      test_size = test_size,
                                                      random_state = 42)
  print(f'Size of data set: {len(X)}')
  print(f'Size of training set: {len(X_train)}')
  print(f'Size of test set: {len(X_test)}')

  # Define the parameter distributions for RandomizedSearchCV
  param_grid = {
      'max_depth': np.arange(2, 8, 1),
      'n_estimators': np.arange(2, max(int(m.ceil(len(X_train)*0.1)),3), 1),
      'max_features': ['sqrt']
  }
  depth_len = param_grid['max_depth'].size
  estimators_len = param_grid['n_estimators'].size

  print(f'Size of grid search: {depth_len * estimators_len}')

  # Create the RandomizedSearchCV object
  grid_search = GridSearchCV(estimator=RandomForestRegressor(random_state=42),
                             param_grid=param_grid,
                             scoring = 'neg_mean_absolute_percentage_error',
                             cv = 5,
                             n_jobs = -1)

  ''' >3 : the fold and candidate parameter indexes
      are also displayed together with the starting time of the computation.
  '''
  # Fit the RandomizedSearchCV object to the data
  grid_search.fit(X_train, y_train)

  # Get the best estimator
  best_estimator = grid_search.best_estimator_

  # Make predictions using the best estimator
  y_pred = best_estimator.predict(X_test)

  # Calculate R^2 score
  r2 = r2_score(y_test, y_pred)

  # Calculate MAE
  mae = mean_absolute_error(y_test, y_pred)

  # Calculate MAPE
  mape = mean_absolute_percentage_error(y_test, y_pred)

  # Calculate RMSE
  rmse = np.sqrt(mean_squared_error(y_test, y_pred))

  # Print the best parameters, best score, and evaluation metrics
  print('Best Parameters: ', grid_search.best_params_)
  print('Training Score (MAPE): ', round(grid_search.best_score_, 3))
  print(10*'-' + 'Test scores' + 10*'-')
  print('R^2 Score:', round(r2, 3))
  print('MAE:', round(mae, 3))
  print('MAPE:', round(mape, 3))
  print('RMSE:', round(rmse, 3))
  print()


  # Create the new row as a DataFrame
  new_row = pd.DataFrame({'HOSPI_CODE_UCD': ['CODE_UCD_'+str(medicine)],
                          'R2': [r2],
                          'RMSE': [rmse],
                          'MAE': [mae],
                          'MAPE': [mape]})

  # Append the new row to the DataFrame
  df_scores = pd.concat([df_scores, new_row], ignore_index=True)

  # plot pred x test
  plot_pred(y_pred, y_test, medicine)
  print()


  plot_mape(y_pred, y_test, medicine)
  print()

  # Return the updated DataFrame
  return df_scores


In [27]:
df_prediction_scores = pd.DataFrame(columns=['HOSPI_CODE_UCD', 'R2', 'RMSE', 'MAE', 'MAPE'])

for medicine in medicines:
  df_prediction_scores = test_1_baseline(df, medicine, df_prediction_scores)

df_prediction_scores


----------------------------------------------------------------------------------------------------
Medicine:3400892088310
Size of data set: 171
Size of training set: 153
Size of test set: 18
Size of grid search: 84
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -2.046
----------Test scores----------
R^2 Score: 0.766
MAE: 655.776
MAPE: 0.174
RMSE: 984.019





----------------------------------------------------------------------------------------------------
Medicine:3400892075761
Size of data set: 204
Size of training set: 183
Size of test set: 21
Size of grid search: 102
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -1.021
----------Test scores----------
R^2 Score: 0.702
MAE: 678.679
MAPE: 0.33
RMSE: 1526.633





----------------------------------------------------------------------------------------------------
Medicine:3400892203645
Size of data set: 200
Size of training set: 180
Size of test set: 20
Size of grid search: 96
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 8}
Training Score (MAPE):  -0.687
----------Test scores----------
R^2 Score: 0.931
MAE: 735.497
MAPE: 1.108
RMSE: 984.944





----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Size of data set: 201
Size of training set: 180
Size of test set: 21
Size of grid search: 96
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 5}
Training Score (MAPE):  -1.09
----------Test scores----------
R^2 Score: 0.918
MAE: 871.008
MAPE: 0.673
RMSE: 1257.679





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Size of data set: 195
Size of training set: 175
Size of test set: 20
Size of grid search: 96
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 5}
Training Score (MAPE):  -1.465
----------Test scores----------
R^2 Score: 0.948
MAE: 488.867
MAPE: 11.749
RMSE: 735.763



...



----------------------------------------------------------------------------------------------------
Medicine:3400893022634
Size of data set: 156
Size of training set: 140
Size of test set: 16
Size of grid search: 72
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 13}
Training Score (MAPE):  -18.817
----------Test scores----------
R^2 Score: 0.739
MAE: 632.661
MAPE: 64.81
RMSE: 842.85





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Size of data set: 201
Size of training set: 180
Size of test set: 21
Size of grid search: 96
Best Parameters:  {'max_depth': 4, 'max_features': 'sqrt', 'n_estimators': 8}
Training Score (MAPE):  -2.105
----------Test scores----------
R^2 Score: 0.985
MAE: 1018.034
MAPE: 1.585
RMSE: 1310.235





----------------------------------------------------------------------------------------------------
Medicine:3400892669236
Size of data set: 173
Size of training set: 155
Size of test set: 18
Size of grid search: 84
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -8.466
----------Test scores----------
R^2 Score: 0.975
MAE: 919.819
MAPE: 2.389
RMSE: 1173.202





----------------------------------------------------------------------------------------------------
Medicine:3400892508566
Size of data set: 190
Size of training set: 171
Size of test set: 19
Size of grid search: 96
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -0.879
----------Test scores----------
R^2 Score: 0.82
MAE: 740.37
MAPE: 0.257
RMSE: 1017.162



HOSPI_CODE_UCD        R2          RMSE          MAE       MAPE
0   CODE_UCD_3400892088310  0.766258    984.018697   655.775996   0.174475
1   CODE_UCD_3400892075761  0.701579   1526.632560   678.678975   0.330208
2   CODE_UCD_3400892203645  0.931360    984.943780   735.496763   1.107614
3   CODE_UCD_3400892065366  0.917614   1257.679148   871.007590   0.672914
4   CODE_UCD_3400892052120  0.948413    735.762539   488.866909  11.749488
5   CODE_UCD_3400891996128  0.956614  11776.003342  8252.248558  20.432358
6   CODE_UCD_3400893826706  0.781640   1271.869451   959.204784   2.887557
7   CODE_UCD_3400893736135  0.873737    736.504814   502.108690   0.113065
8   CODE_UCD_3400893875490  0.799387   2585.180451  1600.886595   0.597244
9   CODE_UCD_3400890837149  0.587180   3969.761338  2075.746457   4.326370
10  CODE_UCD_3400891235203  0.631615    995.526154   532.280407  12.210670
11  CODE_UCD_3400891225037  0.745982   3430.639047  2333.844422   1.940287
12  CODE_UCD_3400891191226  0.933451    737.562665   532.503963   0.566892
13  CODE_UCD_3400892729589  0.836913   2047.178120  1190.874269   1.834193
14  CODE_UCD_3400892745848 -0.038611   4799.022172  2260.272670   0.563487
15  CODE_UCD_3400892697789  0.432943   2337.099932   942.391475   3.420754
16  CODE_UCD_3400892761527  0.957344   2341.785016  1899.991073   0.797840
17  CODE_UCD_3400893022634  0.738849    842.850489   632.660570  64.810440
18  CODE_UCD_3400892761695  0.984937   1310.235341  1018.034019   1.584781
19  CODE_UCD_3400892669236  0.975388   1173.201522   919.819359   2.388712
20  CODE_UCD_3400892508566  0.819637   1017.162374   740.369512   0.256510

In [38]:
def train_test_split_modified(df, random_state = 42, test_size = 0.1, Shuffle = False):
  df_iter = df.copy()

  np.random.seed(random_state)

  X_train = []
  y_train = []

  X_test = []
  y_test = []

  columns = df.columns

  df_train = pd.DataFrame(columns=columns)
  df_test = pd.DataFrame(columns=columns)
  i = 0
  for medicine in df_iter.HOSPI_CODE_UCD.unique():
    df_temp = df_iter[df_iter['HOSPI_CODE_UCD'] == medicine]
    i += len(df_temp)
    n_samples = len(df_temp)


    if n_samples == 1:
      print('Not enough samples in cluster')
      test_samples = 1
    else:
      test_samples = max(m.ceil(n_samples * test_size), 2)


    for _ in range(test_samples):
      random_index = np.random.choice(df_temp.index)
      random_row = df_temp.loc[random_index].to_frame().T

      # Concatenate the new row to the original DataFrame
      df_test = pd.concat([df_test, random_row], ignore_index=False)

      # Remove the selected index from df_temp
      df_temp = df_temp.drop(random_index)

    df_iter = df_iter.drop(df_iter[df_iter['HOSPI_CODE_UCD'] == medicine].index)

  # Get the indices of rows to exclude from df
  exclude_indices = df_test.index

  # Create df_train by dropping the rows specified by the exclude_indices from df
  df_train = df.drop(exclude_indices)

  if shuffle:
    X_train, y_train = shuffle(df_train.drop(['QUANTITY', 'CLUSTER'], axis=1), df_train.QUANTITY.values, random_state = random_state)
    X_test, y_test = shuffle(df_test.drop(['QUANTITY', 'CLUSTER'], axis=1).values, df_test.QUANTITY.values, random_state = random_state)

  return X_train, X_test, y_train, y_test

In [43]:
def test_2_clustering(df, df_scores, medicines):
  for cluster in df.CLUSTER.unique():
    print()
    print(100*'-')
    print(f'Cluster: {cluster}')

    # Perform the train-test split with shuffled samples
    X_train, X_test, y_train, y_test = train_test_split_modified(df[df['CLUSTER'] == cluster].drop(['DATE', 'QUANTITY_MA', 'RESID', 'SEASONAL', 'TREND'], axis=1))
    print(f'Size of data set: {len(X_train) + len(X_test)}')
    print(f'Size of training set: {len(X_train)}')
    print(f'Size of test set: {len(X_test)}')

    df_test = pd.DataFrame(X_test, columns = df.drop(['QUANTITY','CLUSTER','DATE', 'QUANTITY_MA', 'RESID', 'SEASONAL', 'TREND'], axis=1).copy().columns)
    df_test['QUANTITY'] = y_test


    # Define the parameter distributions for RandomizedSearchCV
    param_grid = {
        'max_depth': np.arange(2, 8, 1),
        'n_estimators': np.arange(2, max(int(m.ceil(len(X_train)*0.1)),3), 1),
        'max_features': ['sqrt']
    }

    depth_len = param_grid['max_depth'].size
    estimators_len = param_grid['n_estimators'].size

    print(f'Size of grid search: {depth_len * estimators_len}')

    # Create the RandomizedSearchCV object
    grid_search = GridSearchCV(estimator=RandomForestRegressor(random_state=42),
                              param_grid=param_grid,
                              scoring = 'neg_mean_absolute_percentage_error',
                              cv = 5,
                              n_jobs = -1)

    ''' >3 : the fold and candidate parameter indexes
        are also displayed together with the starting time of the computation.
    '''

    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)

    # Fit the RandomizedSearchCV object to the data
    grid_search.fit(X_train_scaled, y_train)
    print("Finished training")

    # Get the best estimator
    best_estimator = grid_search.best_estimator_

    for medicine in df_test.HOSPI_CODE_UCD.unique():
      print()
      print(100*'-')
      print('Medicine:' + str(medicine))

      X_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine].drop(['QUANTITY'], axis=1).copy().values

      scaler = StandardScaler()
      X_test_scaled = scaler.fit_transform(X_test_medicine)

      y_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine]['QUANTITY'].copy().values

      # Make predictions using the best estimator
      y_pred = best_estimator.predict(X_test_scaled)

      # Calculate R^2 score
      r2 = r2_score(y_test_medicine, y_pred)

      # Calculate MAE
      mae = mean_absolute_error(y_test_medicine, y_pred)

      # Calculate MAPE
      mape = mean_absolute_percentage_error(y_test_medicine, y_pred)

      # Calculate RMSE
      rmse = np.sqrt(mean_squared_error(y_test_medicine, y_pred))

      # Print the best parameters, best score, and evaluation metrics

      # Print the best parameters, best score, and evaluation metrics
      print('Best Parameters: ', grid_search.best_params_)
      print('Training Score (MAPE): ', round(grid_search.best_score_, 3))
      print(10*'-' + 'Test scores' + 10*'-')
      print('R^2 Score:', round(r2, 3))
      print('MAE:', round(mae, 3))
      print('MAPE:', round(mape, 3))
      print('RMSE:', round(rmse, 3))
      print()


      # Create the new row as a DataFrame
      new_row = pd.DataFrame({'CLUSTER': [cluster],
                              'HOSPI_CODE_UCD': ['CODE_UCD_'+str(int(medicine))],
                              'R2': [r2],
                              'RMSE': [rmse],
                              'MAE': [mae],
                              'MAPE': [mape]})

      # Append the new row to the DataFrame
      df_scores = pd.concat([df_scores, new_row], ignore_index=True)

      plot_pred(y_pred, y_test_medicine, medicine)
      print()

      plot_mape(y_pred, y_test_medicine, medicine)
      print()

  # Return the updated DataFrame
  return df_scores

In [44]:
df_prediction_scores_agg = pd.DataFrame(columns=[ 'HOSPI_CODE_UCD', 'CLUSTER', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_agg = test_2_clustering(df_agg_clusters, df_prediction_scores_agg, medicines)

df_prediction_scores_agg


----------------------------------------------------------------------------------------------------
Cluster: 0
Size of data set: 2323
Size of training set: 2082
Size of test set: 241
Size of grid search: 1242
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -4.981
----------Test scores----------
R^2 Score: 0.433
MAE: 3889.309
MAPE: 2.764
RMSE: 5243.081





----------------------------------------------------------------------------------------------------
Medicine:3400891191226
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -4.981
----------Test scores----------
R^2 Score: 0.665
MAE: 964.545
MAPE: 0.214
RMSE: 1679.668





----------------------------------------------------------------------------------------------------
Medicine:3400892729589
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -4.981
----------Test scores----------
R^2 Score: 0.554
MAE: 3744.349
MAPE: 0.321
RMSE: 5219.876





----------------------------------------------------------------------------------------------------
Medicine:3400892052120
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -4.981
----------Test scores----------
R^2 Score: 0.835
MAE: 1109.744
MAPE: 7.591
RMSE: 1334.973





----------------------------------------------------------------------------------------------------
Medicine:3400892745848
Best Parameters:  {'max_depth': 7, 'max_features': 'sqrt', 'n_estimators': 6}
Training Score (MAPE):  -4.981
----------Test scores----------
R^2 Score: 0.651
MAE: 2378.071
MAPE: 0.271
RMSE: 2960.362



...



----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Best Parameters:  {'max_depth': 5, 'max_features': 'sqrt', 'n_estimators': 3}
Training Score (MAPE):  -0.162
----------Test scores----------
R^2 Score: -181.672
MAE: 4420.97
MAPE: 0.565
RMSE: 4433.121





----------------------------------------------------------------------------------------------------
Cluster: 4
Size of data set: 36
Size of training set: 32
Size of test set: 4
Size of grid search: 12
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891225037
Best Parameters:  {'max_depth': 6, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.119
----------Test scores----------
R^2 Score: 0.164
MAE: 3046.922
MAPE: 0.184
RMSE: 3299.71





----------------------------------------------------------------------------------------------------
Cluster: 5
Size of data set: 12
Size of training set: 8
Size of test set: 4
Size of grid search: 6
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400892761527
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.123
----------Test scores----------
R^2 Score: -2.055
MAE: 3469.0
MAPE: 0.105
RMSE: 4229.7





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Best Parameters:  {'max_depth': 2, 'max_features': 'sqrt', 'n_estimators': 2}
Training Score (MAPE):  -0.123
----------Test scores----------
R^2 Score: -22.892
MAE: 6683.5
MAPE: 0.297
RMSE: 6684.286



HOSPI_CODE_UCD CLUSTER          R2          RMSE           MAE  \
0   CODE_UCD_3400892065366       0    0.433055   5243.081071   3889.309052   
1   CODE_UCD_3400891191226       0    0.665021   1679.668376    964.544618   
2   CODE_UCD_3400892729589       0    0.554111   5219.876216   3744.349213   
3   CODE_UCD_3400892052120       0    0.834798   1334.972724   1109.744214   
4   CODE_UCD_3400892745848       0    0.650616   2960.362305   2378.071120   
5   CODE_UCD_3400892508566       0    0.205655   2400.453849   1937.157071   
6   CODE_UCD_3400891235203       0   -1.017779   2891.865903   2085.948174   
7   CODE_UCD_3400892697789       0    0.510320   2003.738799   1593.147503   
8   CODE_UCD_3400892075761       0    0.655270   2183.461402   1911.801790   
9   CODE_UCD_3400890837149       0    0.757009   2875.329460   2021.133211   
10  CODE_UCD_3400893826706       0   -1.230639   2812.438673   2010.421666   
11  CODE_UCD_3400893022634       0   -4.055512   4467.492893   3747.677771   
12  CODE_UCD_3400891225037       0    0.212342   8806.900863   6576.533376   
13  CODE_UCD_3400892669236       0   -0.300344  12034.231287  10477.973470   
14  CODE_UCD_3400892761527       0   -1.221447   5247.034939   4427.389885   
15  CODE_UCD_3400892761695       0    0.329678   3346.900216   2700.306213   
16  CODE_UCD_3400892203645       0    0.743927   1583.507531   1194.102268   
17  CODE_UCD_3400893736135       0   -0.543150   2194.536729   1726.200020   
18  CODE_UCD_3400892088310       0    0.085392   3002.655795   2329.390898   
19  CODE_UCD_3400893875490       0    0.238469   8099.069127   6591.217129   
20  CODE_UCD_3400891225037       2   -3.633110   4788.144961   4226.691136   
21  CODE_UCD_3400892075761       2 -293.525184   3675.880054   2567.971297   
22  CODE_UCD_3400892065366       2  -14.843526   3033.306754   2444.360560   
23  CODE_UCD_3400892697789       2  -65.884994   3736.763669   3091.766533   
24  CODE_UCD_3400892088310       2  -24.241451   1952.897613   1679.166936   
25  CODE_UCD_3400892745848       2 -775.852838   3470.731225   3389.244969   
26  CODE_UCD_3400892203645       2   -9.227325   1357.254373   1151.131516   
27  CODE_UCD_3400893022634       2  -81.567473   2284.132283   1972.292898   
28  CODE_UCD_3400890837149       2  -50.610634   1899.502555   1303.326411   
29  CODE_UCD_3400892052120       2 -730.458309   4641.517680   4127.725536   
30  CODE_UCD_3400893875490       2  -47.308607   8738.534232   8547.176905   
31  CODE_UCD_3400891191226       2   -4.135054   1972.048497   1758.048769   
32  CODE_UCD_3400893736135       2   -0.677900   1855.505582   1502.216811   
33  CODE_UCD_3400891235203       2    0.134462   1969.340105   1814.222848   
34  CODE_UCD_3400892508566       2  -20.401330   2639.252241   2414.110740   
35  CODE_UCD_3400893826706       2   -0.608283   2077.827296   1574.542872   
36  CODE_UCD_3400892729589       2  -27.833348   2490.285844   1867.957884   
37  CODE_UCD_3400892669236       2 -109.332401   6097.185003   5979.150152   
38  CODE_UCD_3400892761527       2         NaN   4398.173110   4398.173110   
39  CODE_UCD_3400892761695       2         NaN   3023.173110   3023.173110   
40  CODE_UCD_3400892761695       3   -2.629299   2268.527808   2195.445501   
41  CODE_UCD_3400892761527       3    0.328651   2513.244829   2006.254738   
42  CODE_UCD_3400891225037       1   -1.133138   3629.408502   2729.367291   
43  CODE_UCD_3400892761695       1  -23.282215   4281.209604   3667.350904   
44  CODE_UCD_3400892669236       1   -9.575188   2906.048904   2681.266566   
45  CODE_UCD_3400893875490       1  -11.042551   3690.233730   3295.565023   
46  CODE_UCD_3400892761527       1  -10.976283   1260.573452   1143.161030   
47  CODE_UCD_3400892065366       1 -181.671782   4433.120913   4420.970146   
48  CODE_UCD_3400891225037       4    0.164270   3299.709584   3046.921875   
49  CODE_UCD_3400892761527       5   -2.054839   4229.699871   3469.000000   
50  CODE_UCD_3400892761695       5

In [ ]:
df_prediction_scores_pca = pd.DataFrame(columns=[ 'HOSPI_CODE_UCD', 'CLUSTER', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_pca = test_2_clustering(df_clustered_pca, df_prediction_scores_pca, medicines)

df_prediction_scores_pca

In [45]:
from sklearn.neural_network import MLPRegressor

def test_2_clustering_MLPR(df, df_scores, medicines):
  for cluster in df.CLUSTER.unique():
    print()
    print(100*'-')
    print(f'Cluster: {cluster}')

    # Perform the train-test split with shuffled samples
    X_train, X_test, y_train, y_test = train_test_split_modified(df[df['CLUSTER'] == cluster].drop(['DATE', 'QUANTITY_MA', 'RESID', 'SEASONAL', 'TREND'], axis=1))
    print(f'Size of data set: {len(X_train) + len(X_test)}')
    print(f'Size of training set: {len(X_train)}')
    print(f'Size of test set: {len(X_test)}')

    df_test = pd.DataFrame(X_test, columns = df.drop(['QUANTITY','CLUSTER','DATE', 'QUANTITY_MA', 'RESID', 'SEASONAL', 'TREND'], axis=1).copy().columns)
    df_test['QUANTITY'] = y_test

    # Define the parameter grid for MLPRegressor
    param_grid = {
        'hidden_layer_sizes': [(100,), (50, 50), (20, 10)],
        'activation': ['relu', 'tanh'],
        'solver': ['adam', 'lbfgs'],
        'max_iter': [1000],
    }

    depth_len = len(param_grid['hidden_layer_sizes']) * len(param_grid['activation']) * \
                len(param_grid['solver']) * len(param_grid['max_iter'])

    print(f'Size of grid search: {depth_len}')

    # Create the MLPRegressor object
    mlp_regressor = MLPRegressor(random_state=42)

    # Create the GridSearchCV object
    grid_search = GridSearchCV(estimator=mlp_regressor, param_grid=param_grid,
                                scoring='neg_mean_absolute_percentage_error',
                                cv=5, n_jobs=-1, verbose=3)

    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)

    # Fit the GridSearchCV object to the data
    grid_search.fit(X_train_scaled, y_train)
    print("Finished training")

    # Get the best estimator
    best_estimator = grid_search.best_estimator_

    for medicine in df_test.HOSPI_CODE_UCD.unique():
        print()
        print(100*'-')
        print('Medicine:' + str(medicine))

        X_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine].drop(['QUANTITY'], axis=1).copy().values

        X_test_scaled = scaler.transform(X_test_medicine)

        y_test_medicine = df_test[df_test['HOSPI_CODE_UCD'] == medicine]['QUANTITY'].copy().values

        # Make predictions using the best estimator
        y_pred = best_estimator.predict(X_test_scaled)

        # Calculate R^2 score
        r2 = r2_score(y_test_medicine, y_pred)

        # Calculate MAE
        mae = mean_absolute_error(y_test_medicine, y_pred)

        # Calculate MAPE
        mape = mean_absolute_percentage_error(y_test_medicine, y_pred)

        # Calculate RMSE
        rmse = np.sqrt(mean_squared_error(y_test_medicine, y_pred))

        # Print the best parameters, best score, and evaluation metrics
        print('Best Parameters: ', grid_search.best_params_)
        print('Training Score (MAPE): ', round(grid_search.best_score_, 3))
        print(10*'-' + 'Test scores' + 10*'-')
        print('R^2 Score:', round(r2, 3))
        print('MAE:', round(mae, 3))
        print('MAPE:', round(mape, 3))
        print('RMSE:', round(rmse, 3))
        print()

        # Create the new row as a DataFrame
        new_row = pd.DataFrame({'CLUSTER': [cluster],
                                'HOSPI_CODE_UCD': ['CODE_UCD_'+str(int(medicine))],
                                'R2': [r2],
                                'RMSE': [rmse],
                                'MAE': [mae],
                                'MAPE': [mape]})

        # Append the new row to the DataFrame
        df_scores = pd.concat([df_scores, new_row], ignore_index=True)

        plot_pred(y_pred, y_test_medicine, medicine)
        print()

        plot_mape(y_pred, y_test_medicine, medicine)
        print()

  # Return the updated DataFrame
  return df_scores

In [46]:
df_prediction_scores_agg = pd.DataFrame(columns=[ 'HOSPI_CODE_UCD', 'CLUSTER', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_agg = test_2_clustering_MLPR(df_agg_clusters, df_prediction_scores_agg, medicines)

df_prediction_scores_agg


----------------------------------------------------------------------------------------------------
Cluster: 0
Size of data set: 2323
Size of training set: 2082
Size of test set: 241
Size of grid search: 12
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400892065366
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -1.261
----------Test scores----------
R^2 Score: -1.248
MAE: 7794.453
MAPE: 1.113
RMSE: 10440.504



/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (1000) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400891191226
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -1.261
----------Test scores----------
R^2 Score: -1.854
MAE: 3951.573
MAPE: 0.958
RMSE: 4902.776



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400892729589
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -1.261
----------Test scores----------
R^2 Score: -1.705
MAE: 10207.183
MAPE: 0.967
RMSE: 12856.667



...



----------------------------------------------------------------------------------------------------
Cluster: 5
Size of data set: 12
Size of training set: 8
Size of test set: 4
Size of grid search: 12
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400892761527
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'lbfgs'}
Training Score (MAPE):  -0.088
----------Test scores----------
R^2 Score: -2.867
MAE: 4097.379
MAPE: 0.125
RMSE: 4758.667



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400892761695
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'lbfgs'}
Training Score (MAPE):  -0.088
----------Test scores----------
R^2 Score: -12.27
MAE: 4790.121
MAPE: 0.217
RMSE: 4981.498



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names



HOSPI_CODE_UCD CLUSTER          R2          RMSE           MAE  \
0   CODE_UCD_3400892065366       0   -1.248076  10440.504077   7794.453363   
1   CODE_UCD_3400891191226       0   -1.854001   4902.775939   3951.572621   
2   CODE_UCD_3400892729589       0   -1.704977  12856.667327  10207.182505   
3   CODE_UCD_3400892052120       0   -0.880574   4504.118133   3100.006510   
4   CODE_UCD_3400892745848       0   -2.768928   9723.044149   8333.916765   
5   CODE_UCD_3400892508566       0   -0.909013   3721.287473   2622.555379   
6   CODE_UCD_3400891235203       0   -0.953666   2845.551790   2007.083432   
7   CODE_UCD_3400892697789       0   -0.484307   3488.565471   1992.715509   
8   CODE_UCD_3400892075761       0   -1.032818   5302.191148   3790.266332   
9   CODE_UCD_3400890837149       0   -0.835884   7903.428050   5348.123470   
10  CODE_UCD_3400893826706       0   -2.116330   3324.223240   2770.102888   
11  CODE_UCD_3400893022634       0   -2.579689   3759.273698   3227.955291   
12  CODE_UCD_3400891225037       0   -1.710753  16338.013005  12979.199609   
13  CODE_UCD_3400892669236       0   -3.528538  22457.853043  19859.031443   
14  CODE_UCD_3400892761527       0   -1.367699   5417.004971   4130.981489   
15  CODE_UCD_3400892761695       0   -0.891609   5622.334569   3882.318931   
16  CODE_UCD_3400892203645       0   -0.910943   4325.753571   2986.644070   
17  CODE_UCD_3400893736135       0   -3.630927   3801.655780   3366.259440   
18  CODE_UCD_3400892088310       0   -1.346576   4809.559474   3643.371322   
19  CODE_UCD_3400893875490       0   -2.038238  16177.158060  13262.612020   
20  CODE_UCD_3400891225037       2  -16.459892   9295.050365   9049.275701   
21  CODE_UCD_3400892075761       2  -88.781403   2029.519865   2020.255758   
22  CODE_UCD_3400892065366       2  -73.940271   6597.023685   6558.741557   
23  CODE_UCD_3400892697789       2  -13.650108   1748.846508   1658.190586   
24  CODE_UCD_3400892088310       2 -142.253987   4652.385330   4630.580939   
25  CODE_UCD_3400892745848       2   -0.973608    174.937136    150.336566   
26  CODE_UCD_3400892203645       2 -141.242051   5061.674735   5042.231414   
27  CODE_UCD_3400893022634       2 -145.025418   3037.602801   3026.486216   
28  CODE_UCD_3400890837149       2 -135.844782   3093.031948   3080.495770   
29  CODE_UCD_3400892052120       2   -7.375845    496.683282    453.866892   
30  CODE_UCD_3400893875490       2 -109.675762  13226.733295  13180.958112   
31  CODE_UCD_3400891191226       2  -32.676414   5050.193467   4978.144107   
32  CODE_UCD_3400893736135       2   -8.819161   4488.656369   4300.249388   
33  CODE_UCD_3400891235203       2   -1.038069   3021.949607   2315.899400   
34  CODE_UCD_3400892508566       2  -49.799983   4066.233407   4024.739224   
35  CODE_UCD_3400893826706       2  -14.260119   6400.400072   6234.790970   
36  CODE_UCD_3400892729589       2 -135.804816   5424.408088   5404.471737   
37  CODE_UCD_3400892669236       2 -286.051099   9834.616851   9816.994599   
38  CODE_UCD_3400892761527       2         NaN   7798.742262   7798.742262   
39  CODE_UCD_3400892761695       2         NaN   6424.026982   6424.026982   
40  CODE_UCD_3400892761695       3   -3.495701   2524.825963   2058.091307   
41  CODE_UCD_3400892761527       3    0.104858   2902.061875   2555.298998   
42  CODE_UCD_3400891225037       1   -2.662410   4755.649681   4054.747697   
43  CODE_UCD_3400892761695       1  -24.931632   4424.225621   4338.081358   
44  CODE_UCD_3400892669236       1   -8.728718   2787.319065   2512.284051   
45  CODE_UCD_3400893875490       1   -5.298459   2668.773998   2428.329088   
46  CODE_UCD_3400892761527       1   -0.567888    456.104841    407.623849   
47  CODE_UCD_3400892065366       1 -140.094093   3896.083539   3882.252303   
48  CODE_UCD_3400891225037       4   -0.278127   4080.652409   3880.175797   
49  CODE_UCD_3400892761527       5   -2.866695   4758.667027   4097.378659   
50  CODE_UCD_3400892761695       5

In [ ]:
df_prediction_scores_pca = pd.DataFrame(columns=[ 'HOSPI_CODE_UCD', 'CLUSTER', 'R2', 'RMSE', 'MAE', 'MAPE'])

df_prediction_scores_pca = test_2_clustering_MLPR(df_clustered_pca, df_prediction_scores_pca, medicines)

df_prediction_scores_pca


----------------------------------------------------------------------------------------------------
Cluster: 0
Size of data set: 2440
Size of training set: 2180
Size of test set: 260
Size of grid search: 12
Fitting 5 folds for each of 12 candidates, totalling 60 fits
Finished training

----------------------------------------------------------------------------------------------------
Medicine:3400891225037.0
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -7.322333777874806e+16
----------Test scores----------
R^2 Score: -0.747
MAE: 6260.384
MAPE: 1.3042869419241098e+17
RMSE: 9426.293



/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning:

Stochastic Optimizer: Maximum iterations (1000) reached and the optimization hasn't converged yet.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400892745848.0
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -7.322333777874806e+16
----------Test scores----------
R^2 Score: -0.59
MAE: 2287.385
MAPE: 1.3043351503823277e+17
RMSE: 3595.572



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400893736135.0
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -7.322333777874806e+16
----------Test scores----------
R^2 Score: -0.805
MAE: 1622.868
MAPE: 1.302657072220243e+17
RMSE: 2298.507



...



----------------------------------------------------------------------------------------------------
Medicine:3400891191226.0
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -1.7350600623423034e+16
----------Test scores----------
R^2 Score: -1.138
MAE: 118.357
MAPE: 1.277
RMSE: 146.203



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Medicine:3400892697789.0
Best Parameters:  {'activation': 'tanh', 'hidden_layer_sizes': (20, 10), 'max_iter': 1000, 'solver': 'adam'}
Training Score (MAPE):  -1.7350600623423034e+16
----------Test scores----------
R^2 Score: 0.0
MAE: 8.213
MAPE: 3.698860866973618e+16
RMSE: 8.376



/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names





----------------------------------------------------------------------------------------------------
Cluster: 1
Size of data set: 244
Size of training set: 204
Size of test set: 40
Size of grid search: 12
Fitting 5 folds for each of 12 candidates, totalling 60 fits
